In [4]:
import traceback
import cv2
import numpy as np
import math

cap = cv.VideoCapture(0)
     
while(1):
        
    try:  #an error comes if it does not find anything in window as it cannot find contour of max area
          #therefore this try error statement
          
        ret, frame = cap.read()
        frame = cv2.flip(frame,1)
        kernel = np.ones((3,3),np.uint8)
        
        #define region of interest
        roi = frame[100:300, 100:300]
        
        
        cv2.rectangle(frame,(100,100),(300,300),(0,255,0),0)    
        hsv = cv2.cvtColor(roi, cv.COLOR_BGR2HSV)
         
    # define range of skin color in HSV
        lower_skin = np.array([0,20,70], dtype=np.uint8)
        upper_skin = np.array([20,255,255], dtype=np.uint8)
        
     #extract skin colur imagw  
        mask = cv2.inRange(hsv, lower_skin, upper_skin)
        
    #extrapolate the hand to fill dark spots within
        mask = cv2.dilate(mask,kernel,iterations = 4)
        
    #blur the image
        mask = cv2.GaussianBlur(mask,(5,5),100) 
     
    #find contours
        contours,hierarchy= cv.findContours(mask,cv2.RETR_TREE,cv2.CHAIN_APPROX_SIMPLE)
        print(contours)
        print(hierarchy)
   #find contour of max area(hand)
        cnt = max(contours, key = lambda x: cv2.contourArea(x))
        
    #approx the contour a little
        epsilon = 0.0005*cv.arcLength(cnt,True)
        approx= cv.approxPolyDP(cnt,epsilon,True)
       
        
    #make convex hull around hand
        hull = cv.convexHull(cnt)
        
     #define area of hull and area of hand
        areahull = cv.contourArea(hull)
        areacnt = cv.contourArea(cnt)
      
    #find the percentage of area not covered by hand in convex hull
        arearatio=((areahull-areacnt)/areacnt)*100
    
     #find the defects in convex hull with respect to hand
        hull = cv.convexHull(approx, returnPoints=False)
        defects = cv.convexityDefects(approx, hull)
        
    # l = no. of defects
        l=0
        
    #code for finding no. of defects due to fingers
        for i in range(defects.shape[0]):
            s,e,f,d = defects[i,0]
            start = tuple(approx[s][0])
            end = tuple(approx[e][0])
            far = tuple(approx[f][0])
            pt= (100,180)
            
            
            # find length of all sides of triangle
            a = math.sqrt((end[0] - start[0])**2 + (end[1] - start[1])**2)
            b = math.sqrt((far[0] - start[0])**2 + (far[1] - start[1])**2)
            c = math.sqrt((end[0] - far[0])**2 + (end[1] - far[1])**2)
            s = (a+b+c)/2
            ar = math.sqrt(s*(s-a)*(s-b)*(s-c))
            
            #distance between point and convex hull
            d=(2*ar)/a
            
            # apply cosine rule here
            angle = math.acos((b**2 + c**2 - a**2)/(2*b*c)) * 57
            
        
            # ignore angles > 90 and ignore points very close to convex hull(they generally come due to noise)
            if angle <= 90 and d>30:
                l += 1
                cv2.circle(roi, far, 3, [255,0,0], -1)
            
            #draw lines around hand
            cv2.line(roi,start, end, [0,255,0], 2)
            
            
        l+=1
        
        #print corresponding gestures which are in their ranges
        font = cv2.FONT_HERSHEY_SIMPLEX
        if l==1:
            if areacnt<2000:
                cv2.putText(frame,'Put hand in the box',(0,50), font, 2, (0,0,255), 3, cv2.LINE_AA)
            else:
                if arearatio<12:
                    cv2.putText(frame,'0',(0,50), font, 2, (0,0,255), 3, cv2.LINE_AA)
                elif arearatio<17.5:
                    cv2.putText(frame,'Best of luck',(0,50), font, 2, (0,0,255), 3, cv2.LINE_AA)
                   
                else:
                    cv2.putText(frame,'1',(0,50), font, 2, (0,0,255), 3, cv2.LINE_AA)
                    
        elif l==2:
            cv2.putText(frame,'2',(0,50), font, 2, (0,0,255), 3, cv2.LINE_AA)
            
        elif l==3:
         
              if arearatio<27:
                    cv2.putText(frame,'3',(0,50), font, 2, (0,0,255), 3, cv2.LINE_AA)
              else:
                    cv2.putText(frame,'ok',(0,50), font, 2, (0,0,255), 3, cv2.LINE_AA)
                    
        elif l==4:
            cv2.putText(frame,'4',(0,50), font, 2, (0,0,255), 3, cv2.LINE_AA)
            
        elif l==5:
            cv2.putText(frame,'5',(0,50), font, 2, (0,0,255), 3, cv2.LINE_AA)
            
        elif l==6:
            cv2.putText(frame,'reposition',(0,50), font, 2, (0,0,255), 3, cv2.LINE_AA)
            
        else :
            cv2.putText(frame,'reposition',(10,50), font, 2, (0,0,255), 3, cv2.LINE_AA)
            
        #show the windows
        cv2.imshow('mask',mask)
        cv2.imshow('frame',frame)
    except Exception:
        traceback.print_exc()
        pass
       # break
        
    
    k = cv2.waitKey(5) & 0xFF
    if k == 27:
        break
    
cv2.destroyAllWindows()
cap.release() 

(array([[[ 94,   0]],

       [[ 93,   1]],

       [[ 92,   1]],

       [[ 92,   2]],

       [[ 91,   3]],

       [[ 86,   3]],

       [[ 86,   6]],

       [[ 85,   7]],

       [[ 84,   7]],

       [[ 84,   8]],

       [[ 83,   9]],

       [[ 80,   9]],

       [[ 80,  19]],

       [[ 79,  20]],

       [[ 78,  20]],

       [[ 78,  22]],

       [[ 77,  23]],

       [[ 76,  23]],

       [[ 76,  25]],

       [[ 75,  26]],

       [[ 74,  26]],

       [[ 74,  28]],

       [[ 73,  29]],

       [[ 72,  29]],

       [[ 72,  30]],

       [[ 71,  31]],

       [[ 70,  31]],

       [[ 68,  33]],

       [[ 68,  42]],

       [[ 67,  43]],

       [[ 62,  43]],

       [[ 62,  51]],

       [[ 61,  52]],

       [[ 60,  52]],

       [[ 60,  53]],

       [[ 59,  54]],

       [[ 58,  54]],

       [[ 58,  62]],

       [[ 57,  63]],

       [[ 56,  63]],

       [[ 56,  64]],

       [[ 55,  65]],

       [[ 54,  65]],

       [[ 54,  67]],

       [[ 53,  68]],

       [[

(array([[[114,   0]],

       [[113,   1]],

       [[113,   2]],

       [[112,   3]],

       [[112,   5]],

       [[111,   6]],

       [[110,   6]],

       [[110,   7]],

       [[109,   8]],

       [[108,   8]],

       [[107,   9]],

       [[104,   9]],

       [[103,  10]],

       [[102,  10]],

       [[102,  11]],

       [[101,  12]],

       [[ 98,  12]],

       [[ 98,  19]],

       [[ 97,  20]],

       [[ 96,  20]],

       [[ 96,  24]],

       [[ 95,  25]],

       [[ 94,  25]],

       [[ 94,  33]],

       [[ 93,  34]],

       [[ 92,  34]],

       [[ 92,  35]],

       [[ 91,  36]],

       [[ 90,  36]],

       [[ 90,  40]],

       [[ 89,  41]],

       [[ 88,  41]],

       [[ 88,  42]],

       [[ 87,  43]],

       [[ 86,  43]],

       [[ 86,  47]],

       [[ 85,  48]],

       [[ 84,  48]],

       [[ 84,  50]],

       [[ 83,  51]],

       [[ 82,  51]],

       [[ 82,  52]],

       [[ 81,  53]],

       [[ 76,  53]],

       [[ 75,  54]],

       [[

(array([[[100,   0]],

       [[100,   1]],

       [[ 99,   2]],

       [[ 98,   2]],

       [[ 98,   4]],

       [[ 97,   5]],

       [[ 96,   5]],

       [[ 95,   6]],

       [[ 94,   6]],

       [[ 93,   7]],

       [[ 92,   7]],

       [[ 92,  12]],

       [[ 91,  13]],

       [[ 90,  13]],

       [[ 90,  15]],

       [[ 89,  16]],

       [[ 88,  16]],

       [[ 88,  26]],

       [[ 87,  27]],

       [[ 84,  27]],

       [[ 82,  29]],

       [[ 82,  31]],

       [[ 81,  32]],

       [[ 80,  32]],

       [[ 80,  37]],

       [[ 79,  38]],

       [[ 78,  38]],

       [[ 78,  41]],

       [[ 77,  42]],

       [[ 74,  42]],

       [[ 74,  44]],

       [[ 72,  46]],

       [[ 70,  46]],

       [[ 70,  48]],

       [[ 69,  49]],

       [[ 69,  50]],

       [[ 68,  51]],

       [[ 68,  52]],

       [[ 67,  53]],

       [[ 66,  53]],

       [[ 66,  56]],

       [[ 65,  57]],

       [[ 64,  57]],

       [[ 63,  58]],

       [[ 62,  58]],

       [[

(array([[[ 94,   0]],

       [[ 94,   4]],

       [[ 93,   5]],

       [[ 92,   5]],

       [[ 92,   7]],

       [[ 91,   8]],

       [[ 90,   8]],

       [[ 90,  10]],

       [[ 89,  11]],

       [[ 88,  11]],

       [[ 87,  12]],

       [[ 86,  12]],

       [[ 86,  13]],

       [[ 85,  14]],

       [[ 84,  14]],

       [[ 84,  15]],

       [[ 83,  16]],

       [[ 82,  16]],

       [[ 82,  23]],

       [[ 81,  24]],

       [[ 80,  24]],

       [[ 80,  26]],

       [[ 79,  27]],

       [[ 78,  27]],

       [[ 77,  28]],

       [[ 76,  28]],

       [[ 75,  29]],

       [[ 74,  29]],

       [[ 74,  30]],

       [[ 73,  31]],

       [[ 72,  31]],

       [[ 72,  34]],

       [[ 71,  35]],

       [[ 70,  35]],

       [[ 70,  38]],

       [[ 69,  39]],

       [[ 68,  39]],

       [[ 68,  41]],

       [[ 67,  42]],

       [[ 66,  42]],

       [[ 66,  50]],

       [[ 65,  51]],

       [[ 64,  51]],

       [[ 64,  53]],

       [[ 63,  54]],

       [[

(array([[[152,   0]],

       [[152,   1]],

       [[151,   2]],

       [[150,   2]],

       [[149,   3]],

       [[146,   3]],

       [[146,   4]],

       [[145,   5]],

       [[144,   5]],

       [[144,   9]],

       [[143,  10]],

       [[142,  10]],

       [[142,  14]],

       [[141,  15]],

       [[140,  15]],

       [[139,  16]],

       [[138,  16]],

       [[137,  17]],

       [[136,  17]],

       [[135,  18]],

       [[134,  18]],

       [[134,  21]],

       [[133,  22]],

       [[132,  22]],

       [[132,  23]],

       [[131,  24]],

       [[130,  24]],

       [[130,  26]],

       [[129,  27]],

       [[128,  27]],

       [[127,  28]],

       [[126,  28]],

       [[126,  48]],

       [[127,  48]],

       [[128,  49]],

       [[128,  61]],

       [[129,  61]],

       [[130,  62]],

       [[130,  64]],

       [[131,  64]],

       [[132,  65]],

       [[143,  65]],

       [[144,  66]],

       [[147,  66]],

       [[148,  67]],

       [[

...

(array([[[ 8, 29]],

       [[ 8, 30]],

       [[ 6, 32]],

       [[ 6, 34]],

       [[ 5, 35]],

       [[ 0, 35]],

       [[ 0, 63]],

       [[ 8, 63]],

       [[ 8, 52]],

       [[ 9, 51]],

       [[ 9, 49]],

       [[10, 48]],

       [[11, 49]],

       [[11, 50]],

       [[25, 50]],

       [[25, 37]],

       [[24, 37]],

       [[23, 36]],

       [[23, 32]],

       [[22, 31]],

       [[22, 29]]], dtype=int32), array([[[193,  12]],

       [[188,  17]],

       [[186,  17]],

       [[179,  24]],

       [[179,  25]],

       [[178,  26]],

       [[178,  27]],

       [[177,  28]],

       [[177,  34]],

       [[176,  35]],

       [[176,  36]],

       [[175,  37]],

       [[175,  38]],

       [[172,  41]],

       [[172,  42]],

       [[171,  43]],

       [[171,  56]],

       [[170,  57]],

       [[167,  57]],

       [[164,  60]],

       [[164,  61]],

       [[163,  62]],

       [[161,  62]],

       [[159,  64]],

       [[159,  66]],

       [[158,  

(array([[[ 0, 34]],

       [[ 0, 54]],

       [[ 2, 54]],

       [[ 3, 55]],

       [[ 3, 60]],

       [[ 4, 61]],

       [[ 4, 62]],

       [[19, 62]],

       [[19, 58]],

       [[20, 57]],

       [[21, 57]],

       [[21, 39]],

       [[20, 39]],

       [[19, 38]],

       [[19, 37]],

       [[12, 37]],

       [[11, 36]],

       [[11, 35]],

       [[10, 35]],

       [[ 9, 34]]], dtype=int32), array([[[ 46,   0]],

       [[ 46,   5]],

       [[ 45,   6]],

       [[ 40,   6]],

       [[ 40,   7]],

       [[ 39,   8]],

       [[ 38,   8]],

       [[ 38,  21]],

       [[ 37,  22]],

       [[ 30,  22]],

       [[ 30,  34]],

       [[ 29,  35]],

       [[ 28,  35]],

       [[ 28,  42]],

       [[ 27,  43]],

       [[ 24,  43]],

       [[ 24,  63]],

       [[ 25,  63]],

       [[ 26,  64]],

       [[ 26,  71]],

       [[ 25,  72]],

       [[ 25,  84]],

       [[ 26,  85]],

       [[ 26,  96]],

       [[ 27,  96]],

       [[ 28,  97]],

       [[ 28,

(array([[[ 46,   0]],

       [[ 45,   1]],

       [[ 42,   1]],

       [[ 42,   2]],

       [[ 41,   3]],

       [[ 34,   3]],

       [[ 34,   4]],

       [[ 33,   5]],

       [[ 30,   5]],

       [[ 30,   7]],

       [[ 29,   8]],

       [[ 28,   8]],

       [[ 28,   9]],

       [[ 27,  10]],

       [[ 26,  10]],

       [[ 26,  23]],

       [[ 29,  23]],

       [[ 30,  24]],

       [[ 30,  25]],

       [[ 32,  27]],

       [[ 32,  30]],

       [[ 31,  31]],

       [[ 28,  31]],

       [[ 28,  42]],

       [[ 27,  43]],

       [[ 26,  43]],

       [[ 25,  42]],

       [[ 12,  42]],

       [[ 11,  41]],

       [[ 11,  40]],

       [[ 12,  39]],

       [[ 13,  39]],

       [[ 14,  38]],

       [[ 15,  38]],

       [[ 15,  26]],

       [[  0,  26]],

       [[  0,  56]],

       [[ 21,  56]],

       [[ 22,  57]],

       [[ 22,  64]],

       [[ 23,  64]],

       [[ 24,  65]],

       [[ 24,  75]],

       [[ 25,  75]],

       [[ 26,  76]],

       [[

(array([[[ 4, 26]],

       [[ 4, 27]],

       [[ 3, 28]],

       [[ 0, 28]],

       [[ 0, 63]],

       [[11, 63]],

       [[12, 62]],

       [[13, 62]],

       [[13, 60]],

       [[14, 59]],

       [[15, 59]],

       [[15, 53]],

       [[16, 52]],

       [[21, 52]],

       [[21, 40]],

       [[22, 39]],

       [[23, 39]],

       [[23, 27]],

       [[21, 27]],

       [[20, 26]]], dtype=int32), array([[[ 74,   0]],

       [[ 74,   1]],

       [[ 73,   2]],

       [[ 58,   2]],

       [[ 58,   5]],

       [[ 57,   6]],

       [[ 46,   6]],

       [[ 46,  12]],

       [[ 45,  13]],

       [[ 40,  13]],

       [[ 40,  14]],

       [[ 39,  15]],

       [[ 38,  15]],

       [[ 38,  50]],

       [[ 43,  50]],

       [[ 44,  51]],

       [[ 45,  51]],

       [[ 46,  52]],

       [[ 46,  54]],

       [[ 45,  55]],

       [[ 44,  55]],

       [[ 43,  56]],

       [[ 42,  56]],

       [[ 42,  68]],

       [[ 41,  69]],

       [[ 40,  69]],

       [[ 40,

(array([[[ 0, 23]],

       [[ 0, 39]],

       [[ 7, 39]],

       [[ 8, 40]],

       [[ 8, 41]],

       [[10, 41]],

       [[11, 42]],

       [[10, 43]],

       [[ 0, 43]],

       [[ 0, 60]],

       [[ 9, 60]],

       [[ 9, 56]],

       [[10, 55]],

       [[11, 55]],

       [[11, 43]],

       [[12, 42]],

       [[23, 42]],

       [[23, 41]],

       [[24, 40]],

       [[25, 40]],

       [[25, 26]],

       [[16, 26]],

       [[15, 25]],

       [[14, 25]],

       [[13, 24]],

       [[13, 23]]], dtype=int32), array([[[ 64,   0]],

       [[ 63,   1]],

       [[ 61,   1]],

       [[ 59,   3]],

       [[ 59,   4]],

       [[ 58,   5]],

       [[ 54,   5]],

       [[ 54,   6]],

       [[ 53,   7]],

       [[ 52,   7]],

       [[ 52,   8]],

       [[ 51,   9]],

       [[ 40,   9]],

       [[ 40,  21]],

       [[ 53,  21]],

       [[ 54,  22]],

       [[ 54,  23]],

       [[ 53,  24]],

       [[ 46,  24]],

       [[ 46,  25]],

       [[ 45,  26]],

   

[ WARN:0] global /tmp/pip-req-build-h45n7_hz/opencv/modules/videoio/src/cap_v4l.cpp (890) open VIDEOIO(V4L2:/dev/video0): can't open camera by index
[ WARN:0] global /tmp/pip-req-build-h45n7_hz/opencv/modules/videoio/src/cap_v4l.cpp (890) open VIDEOIO(V4L2:/dev/video0): can't open camera by index
Traceback (most recent call last):
  File "/tmp/ipykernel_3796/3718821121.py", line 86, in hand_detect
    roi = frame[100:300, 100:300]
TypeError: 'NoneType' object is not subscriptable
[ WARN:0] global /tmp/pip-req-build-h45n7_hz/opencv/modules/videoio/src/cap_v4l.cpp (890) open VIDEOIO(V4L2:/dev/video0): can't open camera by index
Traceback (most recent call last):
  File "/tmp/ipykernel_3796/3718821121.py", line 86, in hand_detect
    roi = frame[100:300, 100:300]
TypeError: 'NoneType' object is not subscriptable
[ WARN:0] global /tmp/pip-req-build-h45n7_hz/opencv/modules/videoio/src/cap_v4l.cpp (890) open VIDEOIO(V4L2:/dev/video0): can't open camera by index
Traceback (most recent call la

[ WARN:0] global /tmp/pip-req-build-h45n7_hz/opencv/modules/videoio/src/cap_v4l.cpp (890) open VIDEOIO(V4L2:/dev/video0): can't open camera by index
Traceback (most recent call last):
  File "/tmp/ipykernel_3796/3718821121.py", line 86, in hand_detect
    roi = frame[100:300, 100:300]
TypeError: 'NoneType' object is not subscriptable
[ WARN:0] global /tmp/pip-req-build-h45n7_hz/opencv/modules/videoio/src/cap_v4l.cpp (890) open VIDEOIO(V4L2:/dev/video0): can't open camera by index
Traceback (most recent call last):
  File "/tmp/ipykernel_3796/3718821121.py", line 86, in hand_detect
    roi = frame[100:300, 100:300]
TypeError: 'NoneType' object is not subscriptable
[ WARN:0] global /tmp/pip-req-build-h45n7_hz/opencv/modules/videoio/src/cap_v4l.cpp (890) open VIDEOIO(V4L2:/dev/video0): can't open camera by index
Traceback (most recent call last):
  File "/tmp/ipykernel_3796/3718821121.py", line 86, in hand_detect
    roi = frame[100:300, 100:300]
TypeError: 'NoneType' object is not subscr

[ WARN:0] global /tmp/pip-req-build-h45n7_hz/opencv/modules/videoio/src/cap_v4l.cpp (890) open VIDEOIO(V4L2:/dev/video0): can't open camera by index
Traceback (most recent call last):
  File "/tmp/ipykernel_3796/3718821121.py", line 86, in hand_detect
    roi = frame[100:300, 100:300]
TypeError: 'NoneType' object is not subscriptable
[ WARN:0] global /tmp/pip-req-build-h45n7_hz/opencv/modules/videoio/src/cap_v4l.cpp (890) open VIDEOIO(V4L2:/dev/video0): can't open camera by index
Traceback (most recent call last):
  File "/tmp/ipykernel_3796/3718821121.py", line 86, in hand_detect
    roi = frame[100:300, 100:300]
TypeError: 'NoneType' object is not subscriptable
[ WARN:0] global /tmp/pip-req-build-h45n7_hz/opencv/modules/videoio/src/cap_v4l.cpp (890) open VIDEOIO(V4L2:/dev/video0): can't open camera by index
Traceback (most recent call last):
  File "/tmp/ipykernel_3796/3718821121.py", line 86, in hand_detect
    roi = frame[100:300, 100:300]
TypeError: 'NoneType' object is not subscr

[ WARN:0] global /tmp/pip-req-build-h45n7_hz/opencv/modules/videoio/src/cap_v4l.cpp (890) open VIDEOIO(V4L2:/dev/video0): can't open camera by index
Traceback (most recent call last):
  File "/tmp/ipykernel_3796/3718821121.py", line 86, in hand_detect
    roi = frame[100:300, 100:300]
TypeError: 'NoneType' object is not subscriptable
[ WARN:0] global /tmp/pip-req-build-h45n7_hz/opencv/modules/videoio/src/cap_v4l.cpp (890) open VIDEOIO(V4L2:/dev/video0): can't open camera by index
Traceback (most recent call last):
  File "/tmp/ipykernel_3796/3718821121.py", line 86, in hand_detect
    roi = frame[100:300, 100:300]
TypeError: 'NoneType' object is not subscriptable
[ WARN:0] global /tmp/pip-req-build-h45n7_hz/opencv/modules/videoio/src/cap_v4l.cpp (890) open VIDEOIO(V4L2:/dev/video0): can't open camera by index
Traceback (most recent call last):
  File "/tmp/ipykernel_3796/3718821121.py", line 86, in hand_detect
    roi = frame[100:300, 100:300]
TypeError: 'NoneType' object is not subscr

[ WARN:0] global /tmp/pip-req-build-h45n7_hz/opencv/modules/videoio/src/cap_v4l.cpp (890) open VIDEOIO(V4L2:/dev/video0): can't open camera by index
Traceback (most recent call last):
  File "/tmp/ipykernel_3796/3718821121.py", line 86, in hand_detect
    roi = frame[100:300, 100:300]
TypeError: 'NoneType' object is not subscriptable
[ WARN:0] global /tmp/pip-req-build-h45n7_hz/opencv/modules/videoio/src/cap_v4l.cpp (890) open VIDEOIO(V4L2:/dev/video0): can't open camera by index
Traceback (most recent call last):
  File "/tmp/ipykernel_3796/3718821121.py", line 86, in hand_detect
    roi = frame[100:300, 100:300]
TypeError: 'NoneType' object is not subscriptable
[ WARN:0] global /tmp/pip-req-build-h45n7_hz/opencv/modules/videoio/src/cap_v4l.cpp (890) open VIDEOIO(V4L2:/dev/video0): can't open camera by index
Traceback (most recent call last):
  File "/tmp/ipykernel_3796/3718821121.py", line 86, in hand_detect
    roi = frame[100:300, 100:300]
TypeError: 'NoneType' object is not subscr

...

[ WARN:0] global /tmp/pip-req-build-h45n7_hz/opencv/modules/videoio/src/cap_v4l.cpp (890) open VIDEOIO(V4L2:/dev/video0): can't open camera by index
Traceback (most recent call last):
  File "/tmp/ipykernel_3796/3718821121.py", line 86, in hand_detect
    roi = frame[100:300, 100:300]
TypeError: 'NoneType' object is not subscriptable
[ WARN:0] global /tmp/pip-req-build-h45n7_hz/opencv/modules/videoio/src/cap_v4l.cpp (890) open VIDEOIO(V4L2:/dev/video0): can't open camera by index
Traceback (most recent call last):
  File "/tmp/ipykernel_3796/3718821121.py", line 86, in hand_detect
    roi = frame[100:300, 100:300]
TypeError: 'NoneType' object is not subscriptable
[ WARN:0] global /tmp/pip-req-build-h45n7_hz/opencv/modules/videoio/src/cap_v4l.cpp (890) open VIDEOIO(V4L2:/dev/video0): can't open camera by index
Traceback (most recent call last):
  File "/tmp/ipykernel_3796/3718821121.py", line 86, in hand_detect
    roi = frame[100:300, 100:300]
TypeError: 'NoneType' object is not subscr

[ WARN:0] global /tmp/pip-req-build-h45n7_hz/opencv/modules/videoio/src/cap_v4l.cpp (890) open VIDEOIO(V4L2:/dev/video0): can't open camera by index
Traceback (most recent call last):
  File "/tmp/ipykernel_3796/3718821121.py", line 86, in hand_detect
    roi = frame[100:300, 100:300]
TypeError: 'NoneType' object is not subscriptable
[ WARN:0] global /tmp/pip-req-build-h45n7_hz/opencv/modules/videoio/src/cap_v4l.cpp (890) open VIDEOIO(V4L2:/dev/video0): can't open camera by index
Traceback (most recent call last):
  File "/tmp/ipykernel_3796/3718821121.py", line 86, in hand_detect
    roi = frame[100:300, 100:300]
TypeError: 'NoneType' object is not subscriptable
[ WARN:0] global /tmp/pip-req-build-h45n7_hz/opencv/modules/videoio/src/cap_v4l.cpp (890) open VIDEOIO(V4L2:/dev/video0): can't open camera by index
Traceback (most recent call last):
  File "/tmp/ipykernel_3796/3718821121.py", line 86, in hand_detect
    roi = frame[100:300, 100:300]
TypeError: 'NoneType' object is not subscr

[ WARN:0] global /tmp/pip-req-build-h45n7_hz/opencv/modules/videoio/src/cap_v4l.cpp (890) open VIDEOIO(V4L2:/dev/video0): can't open camera by index
Traceback (most recent call last):
  File "/tmp/ipykernel_3796/3718821121.py", line 86, in hand_detect
    roi = frame[100:300, 100:300]
TypeError: 'NoneType' object is not subscriptable
[ WARN:0] global /tmp/pip-req-build-h45n7_hz/opencv/modules/videoio/src/cap_v4l.cpp (890) open VIDEOIO(V4L2:/dev/video0): can't open camera by index
Traceback (most recent call last):
  File "/tmp/ipykernel_3796/3718821121.py", line 86, in hand_detect
    roi = frame[100:300, 100:300]
TypeError: 'NoneType' object is not subscriptable
[ WARN:0] global /tmp/pip-req-build-h45n7_hz/opencv/modules/videoio/src/cap_v4l.cpp (890) open VIDEOIO(V4L2:/dev/video0): can't open camera by index
Traceback (most recent call last):
  File "/tmp/ipykernel_3796/3718821121.py", line 86, in hand_detect
    roi = frame[100:300, 100:300]
TypeError: 'NoneType' object is not subscr

[ WARN:0] global /tmp/pip-req-build-h45n7_hz/opencv/modules/videoio/src/cap_v4l.cpp (890) open VIDEOIO(V4L2:/dev/video0): can't open camera by index
Traceback (most recent call last):
  File "/tmp/ipykernel_3796/3718821121.py", line 86, in hand_detect
    roi = frame[100:300, 100:300]
TypeError: 'NoneType' object is not subscriptable
[ WARN:0] global /tmp/pip-req-build-h45n7_hz/opencv/modules/videoio/src/cap_v4l.cpp (890) open VIDEOIO(V4L2:/dev/video0): can't open camera by index
Traceback (most recent call last):
  File "/tmp/ipykernel_3796/3718821121.py", line 86, in hand_detect
    roi = frame[100:300, 100:300]
TypeError: 'NoneType' object is not subscriptable
[ WARN:0] global /tmp/pip-req-build-h45n7_hz/opencv/modules/videoio/src/cap_v4l.cpp (890) open VIDEOIO(V4L2:/dev/video0): can't open camera by index
Traceback (most recent call last):
  File "/tmp/ipykernel_3796/3718821121.py", line 86, in hand_detect
    roi = frame[100:300, 100:300]
TypeError: 'NoneType' object is not subscr

KeyboardInterrupt: 